In [6]:
import pandas as pd
import gensim.downloader as api
from sklearn.metrics.pairwise import cosine_distances
from  sklearn.metrics.pairwise import cosine_similarity

from nltk import word_tokenize, pos_tag
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer 
lemmatizer = WordNetLemmatizer()
from nltk.corpus import stopwords
stopWords = set(stopwords.words('english'))
import math
import numpy as np

from tqdm import tqdm

In [8]:
model = api.load('glove-twitter-100')

KeyboardInterrupt: 

# DEFINE DUNCTIONS

# SYSTRAN EN FR VS EN RU

In [3]:
systran_en_fr = pd.read_csv("systran_en_fr_pos.csv")
systran_en_fr.head()

Unnamed: 0  word local_word   pos  \
0           0  word        mot  noun   
1           1  word     parole  noun   
2           2  word      terme  noun   
3           3  word     propos  noun   
4           4  word    mention  noun   

                                            examples  \
0        key word|last word|signal word|first words|   
1  fine words|word of god|kind word|word of the l...   
2  following words|search word|operative word|eng...   
3    written word|wise words|clear words|warm words|   
4                               words of limitation|   

                                      local_examples  \
0  mot clé | dernier mot | mot indicateur | premi...   
1  belle parole | parole de dieu | aimables parol...   
2  termes suivants | terme de recherche | terme p...   
3  propos écrits ici | propos sages | propos clai...   
4                           mention de limitation |    

                            examples_and_definitions  
0  key word|last word|signal word|first words|ter...  
1  fine words|word of god|kind word|word of the l...  
2  following words|search word|operative word|eng...  
3  written word|wise words|clear words|warm words...  
4  words of limitation|particular | reference | m...

In [5]:
systran_en_ru = pd.read_csv("systran_en_ru_pos.csv")
systran_en_ru.head()

Unnamed: 0  word local_word   pos  \
0           0  word      слово  noun   
1           1   and          и  conj   
2           2   and          а  conj   
3           3   and          и  conj   
4           4   and         но  conj   

                                       examples  \
0   key word|english word|first word|good word|   
1                                    empty_cell   
2                                    empty_cell   
3               He thinks of you day and night|   
4  It's an embarrassing joke and not an insult|   

                                      local_examples  \
0  ключевое слово | английское слово | первое сло...   
1                                         empty_cell   
2                                         empty_cell   
3                     Он думает о вас день и ночь |    
4          Это неуместная шутка, а не оскорбление |    

                            examples_and_definitions  
0  key word|english word|first word|good word|spe...  
1                                         empty_cell  
2                                     but | while |   
3                    He thinks of you day and night|  
4       It's an embarrassing joke and not an insult|

In [9]:
l1 = "hello my friends"
l2 = "hello my girlfriend"

def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return None
    
def get_nonstopwords_vectors_sum(lemm_list):
    orig_vector = np.zeros(shape = 100)
    for lemma in lemm_list:
        if lemma not in stopWords:
            #print (lemma)
            try:
                orig_vector += model[lemma]
            except:
                pass
    return orig_vector


def get_lemmatized_line(line):
    pos_tagged_ngramm = pos_tag(line.split())
    lemmatized_line_list = []
    for word_el in pos_tagged_ngramm:
        pos = get_wordnet_pos(word_el[1])
        if pos:
            lemma = lemmatizer.lemmatize(word_el[0], pos =pos)
        else:
            lemma = word_el[0]
        lemmatized_line_list.append(lemma)
    return lemmatized_line_list

get_lemmatized_line(l1)

def find_lines_similarity(line_1, line_2):
    lemmatized_l1_list = get_lemmatized_line(line_1)
    lemmatized_l2_list = get_lemmatized_line(line_2)
    #print(lemmatized_l1_list,lemmatized_l2_list )
    l1_vect = get_nonstopwords_vectors_sum(lemmatized_l1_list)
    l2_vect = get_nonstopwords_vectors_sum(lemmatized_l2_list)
    cos_sim = cosine_similarity(l1_vect.reshape(1, -1), l2_vect.reshape(1, -1))[0][0]
    #print(cos_sim)
    return cos_sim

find_lines_similarity(l1, l2)    
    

0.9236770700727499

In [11]:
def update_enf_word(dct_word, senseword, pos, exmpl):
    #print(senseword)
    if senseword in dct_word:
        if dct_word[senseword]['pos'] == pos:
            if exmpl == "empty_cell":
                #print("EMPTTY")
                pass
            else:
                dct_word[senseword]['examples'] += exmpl
        if dct_word[senseword]['pos'] != pos:
            if exmpl == "empty_cell":
            #print("EMPTTY")
                pass
            else:
                dct_word[senseword + "_" + pos] = {}
                dct_word[senseword + "_" + pos]['examples'] = exmpl            
    else:
        dct_word[senseword] = {'examples':'', 'pos':''}
        if exmpl == "empty_cell":
            #print("EMPTTY")
            dct_word[senseword]['examples'] = ''
        else:
            dct_word[senseword]['pos'] = pos
            dct_word[senseword]['examples'] = exmpl

def csv_to_structure_dict(df):
    new_dict = {}
    for df_ind in range(len(df)):
        df_element = list(df.iloc[df_ind])
        eng_word = df_element[1]
        sense_word = df_element[2]
        pos = df_element[3]
        examples_context = df_element[6]
        #print(df_element)
        if eng_word not in new_dict:
            new_dict[eng_word] = {}
            update_enf_word(new_dict[eng_word],sense_word, pos, examples_context)
        else:
            update_enf_word(new_dict[eng_word],sense_word, pos, examples_context)
    return new_dict
dct_systran_en_ru = csv_to_structure_dict(systran_en_ru)

In [12]:
dct_systran_en_fr = csv_to_structure_dict(systran_en_fr)

In [13]:
def update_ctx_sim_dict(ctx_ind, dct, simiarity_val):
    if ctx_ind in dct:
        dct[str(ctx_ind)].append(simiarity_val)
    else:
        dct[str(ctx_ind)] = []
        dct[str(ctx_ind)].append(simiarity_val)

In [15]:
c1 = 'gala dinner|romantic dinner|mess dinner|business dinners|'
c2 = 'romantic dinner|gala dinner|family dinner|themed dinner|'
def get_context_similarity(ctx1, ctx2):
    
    #print("ctxs","\n", ctx1,"\n",ctx2 )
    #if "empty_cell" not in ctx1 and "empty_cell" not in ctx2:
    ctx1_similarity_dict = {}
    ctx2_similarity_dict = {}
    ctx1_ind = 0
    if len(ctx1) != 0 and len(ctx2) != 0:
        for ctx1_el in ctx1.split("|"):
            if ctx1_el.strip() != '':
                #print(ctx1_el)
                ctx2_ind = 0
                for ctx1_e2 in ctx2.split("|"):
                    if ctx1_e2.strip() != '': 
                        #print (ctx1_e2.strip())
                        sim = find_lines_similarity(ctx1_el, ctx1_e2) 
                        update_ctx_sim_dict(ctx1_el, ctx1_similarity_dict,sim)
                        update_ctx_sim_dict(ctx1_e2, ctx2_similarity_dict,sim)
                        #print('SIM',ctx1_el, ctx1_e2,sim)
                    #ctx2_ind += 1
            #ctx1_ind += 1
        top_simialrity_list = []
        #print("ctx1", ctx1_similarity_dict)
        for ctx1 in ctx1_similarity_dict.keys():
            ctx1_similarity_dict[ctx1] =sorted(ctx1_similarity_dict[ctx1])[-1]
            top_simialrity_list.append(ctx1_similarity_dict[ctx1])
        #print("ctx1", ctx1_similarity_dict)
        #print("ctx2",ctx2_similarity_dict)
        for ctx2 in ctx2_similarity_dict.keys():
            ctx2_similarity_dict[ctx2] = sorted(ctx2_similarity_dict[ctx2])[-1]
            top_simialrity_list.append(ctx2_similarity_dict[ctx2])
        #print("ctx2",ctx2_similarity_dict)
        #print(top_simialrity_list)
        return np.mean(top_simialrity_list)
    else:
        return "no_ctx"
get_context_similarity(c1, c2)        

0.9299981885542088

In [31]:
def merge_dicts(l1_l2_dict,l2_to_l1, l1_to_l2):
    for local_word_1 in l1_l2_dict.keys():
        sorted_sim = sorted(l1_l2_dict[local_word_1].items(), key=lambda kv: kv[1], reverse = True)
        if sorted_sim[0][1] < 0.4:
            print("no suitable connections for ", local_word_1)
            l1_to_l2[local_word_1] = ["no_equality"]
        else:
            if local_word_1 in l1_to_l2:
                if sorted_sim[0][0] not in l1_to_l2[local_word_1]:
                    l1_to_l2[local_word_1].append(sorted_sim[0][0])
            else:
                l1_to_l2[local_word_1] = []
                l1_to_l2[local_word_1].append(sorted_sim[0][0])
            print(local_word_1, "sorted_sim[0][1]",sorted_sim[0][1])
            
            if sorted_sim[0][0] in l2_to_l1:  
                if local_word_1 not in l2_to_l1[sorted_sim[0][0]]:
                    l2_to_l1[sorted_sim[0][0]].append(local_word_1)
            else:
                l2_to_l1[sorted_sim[0][0]] = []
                l2_to_l1[sorted_sim[0][0]].append(local_word_1)
                
ru_fr_dict = {'обойти': {'se promener': 0.16193252812028638, 'se balader': 0.15641367945030674, "s'éloigner": 0.162819447439424, 'promener': 0.16490256085461272}, 'вращаться': {'se promener': 0.4123024692238632, 'se balader': 0.36482488114980133, "s'éloigner": 0.19768349945429559, 'promener': 0.22889580396221318}, 'ездить по миру': {'se promener': 0, 'se balader': 0, "s'éloigner": 0, 'promener': 0}, 'часто путешествовать': {'se promener': 0, 'se balader': 0, "s'éloigner": 0, 'promener': 0}, 'хватать': {'se promener': 0.36273753561810446, 'se balader': 0.2975160600112141, "s'éloigner": 0.3047695342194968, 'promener': 0.29944649457673916}, 'пролетать': {'se promener': 0.6350658803284455, 'se balader': 0.3733952107024293, "s'éloigner": 0.4256126771370779, 'promener': 0.6414917193832451}, 'ходить вокруг': {'se promener': 0, 'se balader': 0, "s'éloigner": 0, 'promener': 0}}
fr_ru_dict = {'se promener': {'обойти': 0.16193252812028638, 'вращаться': 0.4123024692238632, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.36273753561810446, 'пролетать': 0.6350658803284455, 'ходить вокруг': 0}, 'se balader': {'обойти': 0.15641367945030674, 'вращаться': 0.36482488114980133, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.2975160600112141, 'пролетать': 0.3733952107024293, 'ходить вокруг': 0}, "s'éloigner": {'обойти': 0.162819447439424, 'вращаться': 0.19768349945429559, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.3047695342194968, 'пролетать': 0.4256126771370779, 'ходить вокруг': 0}, 'promener': {'обойти': 0.16490256085461272, 'вращаться': 0.22889580396221318, 'ездить по миру': 0, 'часто путешествовать': 0, 'хватать': 0.29944649457673916, 'пролетать': 0.6414917193832451, 'ходить вокруг': 0}}
def create_matching_structure(l1_l2_dict, l2_l1_dict, l1_to_l2, l2_to_l1):
    print("FIRST LANG TO SECOND")
    merge_dicts(l1_l2_dict, l1_to_l2, l2_to_l1)

    print('\n',l1_to_l2)
    print()
    print(l2_to_l1)
    print("\nSECOND LANG TO FIRST")
    merge_dicts(l2_l1_dict, l2_to_l1, l1_to_l2)
    print('\n',l1_to_l2)
    print()
    print(l2_to_l1)
    print()

l1_to_l2_connect = {}
l2_to_l1_connect = {}

create_matching_structure(ru_fr_dict, fr_ru_dict,l1_to_l2_connect, l2_to_l1_connect)    
    

FIRST LANG TO SECOND
no suitable connections for  обойти
вращаться sorted_sim[0][1] 0.4123024692238632
no suitable connections for  ездить по миру
no suitable connections for  часто путешествовать
no suitable connections for  хватать
пролетать sorted_sim[0][1] 0.6414917193832451
no suitable connections for  ходить вокруг

 {'se promener': ['вращаться'], 'promener': ['пролетать']}

{'обойти': ['no_equality'], 'вращаться': ['se promener'], 'ездить по миру': ['no_equality'], 'часто путешествовать': ['no_equality'], 'хватать': ['no_equality'], 'пролетать': ['promener'], 'ходить вокруг': ['no_equality']}

SECOND LANG TO FIRST
se promener sorted_sim[0][1] 0.6350658803284455
no suitable connections for  se balader
s'éloigner sorted_sim[0][1] 0.4256126771370779
promener sorted_sim[0][1] 0.6414917193832451

 {'se promener': ['вращаться', 'пролетать'], 'promener': ['пролетать'], 'se balader': ['no_equality'], "s'éloigner": ['пролетать']}

{'обойти': ['no_equality'], 'вращаться': ['se promener'],

In [36]:
def merge_entities_lists(l1_to_l2, l2_to_l1, eng_word_list, l1_list, l1_context, l2_list, l2_context, english_word):
    handled_pairs = []
    handle_pairs(l1_to_l2,handled_pairs,
                 eng_word_list,
                 l1_list,l1_context, 
                 l2_list, l2_context, 
                 english_word)
    handle_pairs(l2_to_l1,handled_pairs,eng_word_list, 
                 l2_list, l2_context, 
                 l1_list,l1_context,
                 english_word)                  
    

In [37]:
def get_context_and_examples_sim(senseword_dict_l1, senseword_dict_l2, simil_dict_1,simil_dict_2, 
                                 loc_w_1, loc_w_2, print_output = True):
    if print_output: print(loc_w_1, senseword_dict_l1,"\n", loc_w_2, senseword_dict_l2)
    if senseword_dict_l1['examples'] and senseword_dict_l2['examples']:
        similarity = get_context_similarity(senseword_dict_l1['examples'], senseword_dict_l2['examples'])
    else:
        similarity = 0
    if print_output: print(loc_w_1, loc_w_2, "examples_sim", similarity,"\n")
        
    if similarity == "no_ctx":
        simil_dict_1[loc_w_1][loc_w_2] = 0
        simil_dict_2[loc_w_2][loc_w_1] = 0
    else:
        simil_dict_1[loc_w_1][loc_w_2] = similarity
        simil_dict_2[loc_w_2][loc_w_1] = similarity

        
def merge_two_lang_structures(original_eng_word, lang_dict_1, lang_dict_2,eng_word_df, l1_list_for_df,context_l1,  l2_list_for_df, context_l2):
    sim_dict_l1 = {}
    sim_dict_l2 = {}
    for local_1_senseword in lang_dict_1.keys():
        local_1_senseword_pos = lang_dict_1[local_1_senseword]['pos']
        for local_2_senseword in lang_dict_2.keys():
            local_2_senseword_pos = lang_dict_2[local_2_senseword]['pos']
            if local_2_senseword_pos == local_1_senseword_pos:
                if local_1_senseword not in sim_dict_l1:
                    sim_dict_l1[local_1_senseword] = {}
                if local_2_senseword not in sim_dict_l2:
                    sim_dict_l2[local_2_senseword] = {}
                get_context_and_examples_sim(lang_dict_1[local_1_senseword], lang_dict_2[local_2_senseword],
                                                  sim_dict_l1,sim_dict_l2, local_1_senseword, local_2_senseword)
            
            #break
        #break
    print("INNER_MERGER_DICT")
    print(sim_dict_l1)
    print()
    print(sim_dict_l2)
    print("=======\n")
    
    #MATCHING STRUCTURES FOR ONE ENGLISH WORD
    l1_to_l2_connect = {}
    l2_to_l1_connect = {}
    create_matching_structure(sim_dict_l1, sim_dict_l2,l1_to_l2_connect, l2_to_l1_connect)  
    merge_entities_lists(l1_to_l2_connect, l2_to_l1_connect, eng_word_df, l1_list_for_df, context_l1, l2_list_for_df, context_l2, original_eng_word)
#necessary

In [34]:
l1_to_l2_connect

{'se promener': ['вращаться', 'пролетать'],
 'promener': ['пролетать'],
 'se balader': ['no_equality'],
 "s'éloigner": ['пролетать']}

In [35]:
l2_to_l1_connect

{'обойти': ['no_equality'],
 'вращаться': ['se promener'],
 'ездить по миру': ['no_equality'],
 'часто путешествовать': ['no_equality'],
 'хватать': ['no_equality'],
 'пролетать': ['promener', 'se promener', "s'éloigner"],
 'ходить вокруг': ['no_equality']}

In [19]:
def get_context_from_global_variable_dict_systran(eng_word,local_word):
    #print(dct[eng_word])
    #print(dct_en_fr[eng_word])
    l1_sensewords = list(dct_systran_en_ru[eng_word].keys())
    l2_sensewords = list(dct_systran_en_fr[eng_word].keys())
    if local_word == "no_equality":
        pass
    elif local_word in l1_sensewords:
        print("all_clear", local_word)
        return dct_systran_en_ru[eng_word][local_word]['examples']
    elif local_word in l2_sensewords:
        print("all_clear", local_word)
        return dct_systran_en_fr[eng_word][local_word]['examples']
    else:
        print("something_went_ne_tak_no_word_in_dict", local_word)
    #print(l1_sensewords)
    #print(l2_sensewords)
get_context_from_global_variable_dict_systran("treat", "угощение")    
    

all_clear угощение


'morning treat|feast | '

In [44]:
def handle_pairs(l1_to_l2, handled_pairs, eng_word_list, l1_list,l1_cont, l2_list,l2_cont, english_word):
    for l1_word in l1_to_l2.keys():
        print(l1_word)
        for l2_word in l1_to_l2[l1_word]:
            pair = l1_word + "_" + l2_word
            rev_pair = l2_word + "_" + l1_word
            if pair not in handled_pairs and rev_pair not in handled_pairs:
                print(pair, "not_handled_yet")
                eng_word_list.append(english_word)
                l1_list.append(l1_word)
                #l1_context = get_context_from_global_variable_dict_systran(english_word, l1_word)    
                l1_context = get_context_from_global_variable_dict_azure(english_word, l1_word) 
                l1_cont.append(l1_context)
                l2_list.append(l2_word)
                #l2_context = get_context_from_global_variable_dict_systran(english_word, l2_word) 
                l2_context = get_context_from_global_variable_dict_azure(english_word, l2_word)
                l2_cont.append(l2_context)
                handled_pairs.append(pair)
                handled_pairs.append(rev_pair)
            else:
                print(pair, "already_handled")
            print("handled_pairs",handled_pairs)

In [29]:
def merge_two_dct(big_dict_l1, big_dict_l2, print_output = False):
    count = 0
    global_merged_dict= {}
    eng_word_for_df = []
    l1_list_for_df = [] 
    context_from_l1_list = []
    l2_list_for_df = []
    context_from_l2_list = []
    for eng_word in tqdm(list(big_dict_l1.keys())[15:]):
        print("pricessinf word", eng_word)
        #if eng_word == "necessary":
#         merge_two_lang_structures(eng_word, big_dict_l1[eng_word], big_dict_l2[eng_word],
#                                    eng_word_for_df, l1_list_for_df, 
#                                    context_from_l1_list, l2_list_for_df, context_from_l2_list)
        
        try:
            merge_two_lang_structures(eng_word, big_dict_l1[eng_word], big_dict_l2[eng_word],
                                      eng_word_for_df, l1_list_for_df, context_from_l1_list, 
                                      l2_list_for_df, context_from_l2_list)
        except:
            print(eng_word, 'MERGE_PROBLEM')
        
        count += 1
        #if count > 2: break
    print(len(eng_word_for_df), len(l1_list_for_df), len(l2_list_for_df))
    data = pd.DataFrame(list(zip(eng_word_for_df, l1_list_for_df,context_from_l1_list, l2_list_for_df, context_from_l2_list)),columns =['eng_word', 'l1','l1_context', 'l2','l2_context'])
    print(data.head())
    return  data   
df_all_words_systan = merge_two_dct(dct_systran_en_ru,dct_systran_en_fr)



  0%|          | 0/228 [00:00<?, ?it/s]

pricessinf word treat
угощение {'examples': 'morning treat|feast | ', 'pos': 'noun'} 
 friandise {'examples': 'real treat|natural pet treats|sweet | candy | delicacy | goody | pet treats | ', 'pos': 'noun'}
угощение friandise examples_sim 0.6143912764680798 

угощение {'examples': 'morning treat|feast | ', 'pos': 'noun'} 
 régal {'examples': 'real treat for the eyes|delight | feast | real treat | special treat | ', 'pos': 'noun'}
угощение régal examples_sim 0.8486399288097358 

угощение {'examples': 'morning treat|feast | ', 'pos': 'noun'} 
 gâterie {'examples': 'wholesome treat|sweet treats|', 'pos': 'noun'}
угощение gâterie examples_sim 0.7490667475772732 

угощение {'examples': 'morning treat|feast | ', 'pos': 'noun'} 
 délice {'examples': 'delight | delicacy | bliss | delicious treats | ', 'pos': 'noun'}
угощение délice examples_sim 0.6162675060518669 

угощение {'examples': 'morning treat|feast | ', 'pos': 'noun'} 
 festin {'examples': 'feast | banquet | ', 'pos': 'noun'}
угощение

обращаться considérer examples_sim 0.6280350717388509 

обращаться {'examples': 'turn | contact | apply | appeal | address | deal | turn | reach out | ', 'pos': 'verb'} 
 soigner {'examples': 'to treat people|to treat angina|cure | heal | look after | care | look after | heal | care | ', 'pos': 'verb'}
обращаться soigner examples_sim 0.5706714116089165 

вылечить {'examples': 'cure | heal | ', 'pos': 'verb'} 
 traiter {'examples': 'to treat cancer|to treat disease|to treat diabetes|to treat depression|process | address | deal | handle | discuss | cover | process | ', 'pos': 'verb'}
вылечить traiter examples_sim 0.48822032271513943 

вылечить {'examples': 'cure | heal | ', 'pos': 'verb'} 
 considérer {'examples': 'treated on a case-by-case basis|treated confidentially|treat as error|treated as a contempt|consider | regard | see | view | believe | look | think | feel | ', 'pos': 'verb'}
вылечить considérer examples_sim 0.4107736364071907 

вылечить {'examples': 'cure | heal | ', 'pos': '


  0%|          | 1/228 [00:01<07:07,  1.89s/it]

обрабатывать traiter examples_sim 0.7307608129106613 

обрабатывать {'examples': 'to treat even vast skin areas|process | handle | process | handle | machine | cultivate | ', 'pos': 'verb'} 
 considérer {'examples': 'treated on a case-by-case basis|treated confidentially|treat as error|treated as a contempt|consider | regard | see | view | believe | look | think | feel | ', 'pos': 'verb'}
обрабатывать considérer examples_sim 0.6269695999371799 

обрабатывать {'examples': 'to treat even vast skin areas|process | handle | process | handle | machine | cultivate | ', 'pos': 'verb'} 
 soigner {'examples': 'to treat people|to treat angina|cure | heal | look after | care | look after | heal | care | ', 'pos': 'verb'}
обрабатывать soigner examples_sim 0.6035584133883587 

INNER_MERGER_DICT
{'угощение': {'friandise': 0.6143912764680798, 'régal': 0.8486399288097358, 'gâterie': 0.7490667475772732, 'délice': 0.6162675060518669, 'festin': 0.743992855432116, 'douceur': 0.3151530315580567, 'émail': 0

...


 99%|█████████▉| 226/228 [04:50<00:01,  1.21it/s]

отель best best examples_sim 0.0 

отель best {'examples': 'Hotel Best|', 'pos': 'noun'} 
 must {'examples': 'best for business|must | must-have | best features | absolute must | ', 'pos': 'noun'}
отель best must examples_sim 0.0 

отель best {'examples': 'Hotel Best|', 'pos': 'noun'} 
 meilleur {'examples': 'best of the web|', 'pos': 'noun'}
отель best meilleur examples_sim 0.0 

мерея {'examples': 'extent | ', 'pos': 'noun'} 
 bonne chance {'examples': 'best of luck|', 'pos': 'noun'}
мерея bonne chance examples_sim 0.21738643607743496 

мерея {'examples': 'extent | ', 'pos': 'noun'} 
 maximum {'examples': 'maximum | utmost | minimum | peak | ', 'pos': 'noun'}
мерея maximum examples_sim 0.4748084009009143 

мерея {'examples': 'extent | ', 'pos': 'noun'} 
 best {'examples': 'best-seller | ', 'pos': 'noun'}
мерея best examples_sim 0.12694548090769717 

мерея {'examples': 'extent | ', 'pos': 'noun'} 
 must {'examples': 'best for business|must | must-have | best features | absolute must |

хороший excellent examples_sim 0.9321876508622421 

хороший {'examples': 'very good|really good|especially good|pretty good|nice | great | fine | ', 'pos': 'adj'} 
 positif {'examples': 'particularly good|extremely good|positive | ', 'pos': 'adj'}
хороший positif examples_sim 0.8518463263410659 

хороший {'examples': 'very good|really good|especially good|pretty good|nice | great | fine | ', 'pos': 'adj'} 
 beau {'examples': 'almost too good|fairly good|beautiful | nice | fine | lovely | great | attractive | pretty | wonderful | ', 'pos': 'adj'}
хороший beau examples_sim 0.9192224817937398 

добрый {'examples': 'kind | good-natured | ', 'pos': 'adj'} 
 bon {'examples': 'pretty good|so good|really good|good enough|best | better | right | bad | great | proper | improved | correct | ', 'pos': 'adj'}
добрый bon examples_sim 0.6401298091771368 

добрый {'examples': 'kind | good-natured | ', 'pos': 'adj'} 
 excellent {'examples': 'excellent | great | very good | outstanding | fine | ', 'pos'


100%|██████████| 228/228 [04:51<00:00,  1.28s/it]

правильный bon examples_sim 0.8169685813034102 

правильный {'examples': 'right | correct | proper | true | appropriate | valid | accurate | ', 'pos': 'adj'} 
 excellent {'examples': 'excellent | great | very good | outstanding | fine | ', 'pos': 'adj'}
правильный excellent examples_sim 0.6285355721006357 

правильный {'examples': 'right | correct | proper | true | appropriate | valid | accurate | ', 'pos': 'adj'} 
 positif {'examples': 'particularly good|extremely good|positive | ', 'pos': 'adj'}
правильный positif examples_sim 0.6461667262184323 

правильный {'examples': 'right | correct | proper | true | appropriate | valid | accurate | ', 'pos': 'adj'} 
 beau {'examples': 'almost too good|fairly good|beautiful | nice | fine | lovely | great | attractive | pretty | wonderful | ', 'pos': 'adj'}
правильный beau examples_sim 0.6729924290510085 

INNER_MERGER_DICT
{'хороший': {'bon': 0.883846334467016, 'excellent': 0.9321876508622421, 'positif': 0.8518463263410659, 'beau': 0.91922248179

In [30]:
df_all_words_systan.head()

eng_word       l1                                         l1_context  \
0    treat    régal  real treat for the eyes|delight | feast | real...   
1    treat    régal  real treat for the eyes|delight | feast | real...   
2    treat   délice   delight | delicacy | bliss | delicious treats |    
3    treat   délice   delight | delicacy | bliss | delicious treats |    
4    treat  soigner  to treat people|to treat angina|cure | heal | ...   

             l2                                         l2_context  
0      угощение                             morning treat|feast |   
1  удовольствие  pleasure | fun | satisfaction | enjoyment | am...  
2     лакомство                               delicacy | dainty |   
3  удовольствие  pleasure | fun | satisfaction | enjoyment | am...  
4        лечить       to treat people|heal | cure | heal | dose |

In [48]:
df_all_words_systan.to_csv("systran_ctx_merge_mean_top_sim.csv")

# MERGE AZURE EN FR EN RU

In [43]:
def get_context_from_global_variable_dict_azure(eng_word,local_word):
    #print(dct[eng_word])
    #print(dct_en_fr[eng_word])
    l1_sensewords = list(dct_en_ru_azure[eng_word].keys())
    #l1_sensewords = list(dct[eng_word].keys())
    #l2_sensewords = list(dct_en_fr[eng_word].keys())
    l2_sensewords = list(dct_en_fr_azure[eng_word].keys())
    if local_word == "no_equality":
        pass
    elif local_word in l1_sensewords:
        print("all_clear", local_word)
        return dct_en_ru_azure[eng_word][local_word]['examples']
        #return dct[eng_word][local_word]['examples']
    elif local_word in l2_sensewords:
        print("all_clear", local_word)
        return dct_en_fr_azure[eng_word][local_word]['examples']
        #return dct_en_fr[eng_word][local_word]['examples']
    else:
        print("something_went_ne_tak_no_word_in_dict", local_word)
    #print(l1_sensewords)
    #print(l2_sensewords)
get_context_from_global_variable_dict_azure("treat", "угощение")    
    

all_clear угощение


"treat | refreshments | I just want my treat. | A simple but delightfully sweet treat. | Take the shortcuts and play trick or treat with neighbors! | What about our treat! | Open the door and see your treat. | And she always gets a treat. | I got a special treat for you. | ... guest and they gave me a treat. | ... a restaurant hit, and treat for the family table. | My treat, my treat. | My treat, my treat. | A real chocolate treat for demanding chocolate fans! | This is kind of a treat from the restaurant. | All the kinsfolk and friends gather for the treat. | This morning treat is served in the villas' ancient cellars ... | "

In [39]:
azure_en_ru = pd.read_csv("lookup_azure_en_ru.csv")
azure_en_ru.head()

Unnamed: 0  word      local_word   pos examples local_examples  \
0           0  word           слово  NOUN     NOUN           NOUN   
1           1  word  microsoft word  NOUN     NOUN           NOUN   
2           2  word       текстовый  NOUN     NOUN           NOUN   
3           3  word      поговорить  NOUN     NOUN           NOUN   
4           4   the               в   DET      DET            DET   

                            examples_and_definitions  
0  word | floor | words | But i need your word. |...  
1  word | Per snapshot image size and placement c...  
2  text | word | Word processing applications all...  
3  talk | speak | word | chat | I need to have a ...  
4  in | the | The restaurant serves dinner as an ...

In [40]:
dct_en_ru_azure = csv_to_structure_dict(azure_en_ru)

In [41]:
azure_en_fr = pd.read_csv("lookup_azure_en_fr.csv")
azure_en_fr.head()

Unnamed: 0  word local_word    pos examples local_examples  \
0           0  word    conseil   NOUN     NOUN           NOUN   
1           1  word  nouvelles  OTHER    OTHER          OTHER   
2           2  word        mot   NOUN     NOUN           NOUN   
3           3  word    paroles  OTHER    OTHER          OTHER   
4           4  word     parole  OTHER    OTHER          OTHER   

                            examples_and_definitions  
0  national security council | council | board | ...  
1  news | word | stop press | breaking news | I w...  
2  line | note | code word | word | password | ro...  
3  word | talk | lyrics | lyric | pep talk | utte...  
4  word | faith | speech | gospel truth | spoken ...

In [42]:
dct_en_fr_azure = csv_to_structure_dict(azure_en_fr)

In [45]:
df_all_words_azure = merge_two_dct(dct_en_ru_azure,dct_en_fr_azure)  



  0%|          | 0/182 [00:00<?, ?it/s]

pricessinf word necessary
необходимые {'examples': 'necessary | required | needed | essential | appropriate | desired | Continue specifying points to draft the run as necessary. | Make the necessary changes to the display of the part. | Follow the standard installation steps as necessary. | All necessary attribute definitions are automatically placed. | The customer imports the package and installs the necessary certificates. | Check any related items, and perform the necessary procedures. | Includes all necessary mounting for quick installation. | Are you entering all the necessary data? | Create the tasks necessary to implement the change request. | Click edit and make any necessary changes. | Change the sheet properties as necessary. | Choose another file containing all of the necessary data. | Over time, gathered the necessary human potential and knowledge. | Necessary tools of the trade. | Use this time to make necessary changes! | ', 'pos': 'ADJ'} 
 nécessaire {'examples': 'neces

обязательно inévitable examples_sim 0.6456578272353363 

нужно {'examples': 'need | should | want | needs | must | needed | gotta | necessary | Therefore it is necessary to analyse our mistakes. | It is to me necessary to think about it. | If necessary, rename the constructs. | If necessary, we can also assemble it. | It is not necessary to activate them. | I knew, it is necessary to look after you. | Why is it necessary to have my clock movement cleaned? | Create the source dataset if necessary. | They are all used when necessary. | It is not necessary to create query. | I will do whatever is necessary. | There are no additional steps necessary. | Is it necessary to meet colleagues coming from other cities? | And very necessary was this. | This is necessary to prevent damage of teeth. | ', 'pos': 'ADJ'} 
 nécessaire {'examples': 'necessary | writing case | The Army needs men who are willing to fight, when necessary. | It is not necessary to explain everything. | Is it necessary for ev

требуется inévitable examples_sim 0.6588149886519135 

надо {'examples': "should | necessary | Nothing is necessary to me. | So what you did was necessary. | Also it is necessary to understand that it means. | You are not told in advance where necessary. | After such bath is necessary to have rest. | I you later way to transfer necessary! | It is necessary to say three times. | The doctor said it is necessary. | Is it necessary to buy workbooks? | Only it is not necessary to swear! | He would have written everything that was necessary. | It is necessary to hold an inquiry on the spot. | It is necessary anymore to know about him. | Although he can be very strict when it's necessary. | I said it's not necessary. | ", 'pos': 'ADJ'} 
 nécessaire {'examples': 'necessary | writing case | The Army needs men who are willing to fight, when necessary. | It is not necessary to explain everything. | Is it necessary for everyone to be there? | We gathered the necessary supplies. | It is necessary t


  1%|          | 1/182 [00:05<17:18,  5.74s/it]

...

до devant examples_sim 0.5240530600662916 

INNER_MERGER_DICT
{'перед': {'devant': 0.619009152115729}, 'прежде чем': {'devant': 0.6176852926046188}, 'до': {'devant': 0.5240530600662916}}

{'devant': {'перед': 0.619009152115729, 'прежде чем': 0.6176852926046188, 'до': 0.5240530600662916}}

FIRST LANG TO SECOND
перед sorted_sim[0][1] 0.619009152115729
прежде чем sorted_sim[0][1] 0.6176852926046188
до sorted_sim[0][1] 0.5240530600662916

 {'devant': ['перед', 'прежде чем', 'до']}

{'перед': ['devant'], 'прежде чем': ['devant'], 'до': ['devant']}

SECOND LANG TO FIRST
devant sorted_sim[0][1] 0.619009152115729

 {'devant': ['перед', 'прежде чем', 'до']}

{'перед': ['devant'], 'прежде чем': ['devant'], 'до': ['devant']}

devant
devant_перед not_handled_yet
all_clear devant
all_clear перед
handled_pairs ['devant_перед', 'перед_devant']
devant_прежде чем not_handled_yet
all_clear devant
all_clear прежде чем
handled_pairs ['devant_перед', 'перед_devant', 'devant_прежде чем', 'прежде чем_devant'


 99%|█████████▉| 180/182 [13:48<00:06,  3.16s/it]

за en retard examples_sim 0.7566555620692608 

за {'examples': "for | per | behind | I will not stop until those lips are behind bars! | Just stay behind the yellow tape. | The senior residents stand behind you. | Outside the door, or behind the bar? | Can you just put your hands behind your back? | She did nail him behind your back. | No need to worry about the science behind it. | I prefer staying behind the scenes. | If they remain behind the sun. | You got a glimpse behind the curtain. | And maybe behind that tree over there. | So you're the man behind all this? | Put your hands behind your back, please. | We just did it behind your back. | Follow five metres behind me. | ", 'pos': 'PREP'} 
 en retard sur {'examples': 'behind | We’re behind them in technology. | ', 'pos': 'PREP'}
за en retard sur examples_sim 0.782585472130549 

INNER_MERGER_DICT
{'позади': {'avec': 0.7589793478408197, 'juste derrière': 0.8812413761486368, 'en retard': 0.8304380251100006, 'en retard sur': 0.8657435


100%|██████████| 182/182 [13:48<00:00,  4.55s/it]

под inférieur examples_sim 0.5824465709139657 

INNER_MERGER_DICT
{'под': {'inférieur': 0.5824465709139657}}

{'inférieur': {'под': 0.5824465709139657}}

FIRST LANG TO SECOND
под sorted_sim[0][1] 0.5824465709139657

 {'inférieur': ['под']}

{'под': ['inférieur']}

SECOND LANG TO FIRST
inférieur sorted_sim[0][1] 0.5824465709139657

 {'inférieur': ['под']}

{'под': ['inférieur']}

inférieur
inférieur_под not_handled_yet
all_clear inférieur
all_clear под
handled_pairs ['inférieur_под', 'под_inférieur']
под
под_inférieur already_handled
handled_pairs ['inférieur_под', 'под_inférieur']
pricessinf word best
INNER_MERGER_DICT
{}

{}

FIRST LANG TO SECOND

 {}

{}

SECOND LANG TO FIRST

 {}

{}

1142 1142 1142
    eng_word          l1                                         l1_context  \
0  necessary  nécessaire  necessary | writing case | The Army needs men ...   
1  necessary  nécessaire  necessary | writing case | The Army needs men ...   
2  necessary  nécessaire  necessary | writing case 

In [49]:
df_all_words_azure.head(100)

eng_word                   l1  \
0    necessary           nécessaire   
1    necessary           nécessaire   
2    necessary           nécessaire   
3    necessary           nécessaire   
4    necessary           nécessaire   
5    necessary        si nécessaire   
6    necessary       mal nécessaire   
7    necessary           inévitable   
8           go               partir   
9           go               partir   
10          go               partir   
11          go               partir   
12          go               partir   
13          go               partir   
14          go          être permis   
15          go          être permis   
16          go            se mettre   
17          go            se mettre   
18          go            se mettre   
19          go            se passer   
20          go            se passer   
21          go  aller aux toilettes   
22          go  aller aux toilettes   
23          go                faire   
24          go          qui reste à   
25          go               passer   
26          go   faire une activité   
27          go                aller   
28          go              devenir   
29          go            se vendre   
..         ...                  ...   
70      entire               entier   
71      entire               entier   
72      entire                 tout   
73     Belgium             belgique   
74    anything          tout ce que   
75    anything          tout ce que   
76    anything          tout ce que   
77    anything          tout ce que   
78    anything                comme   
79    anything                 rien   
80  background             contexte   
81  background             contexte   
82  background             contexte   
83  background             contexte   
84  background             origines   
85  background               milieu   
86  background                 fond   
87  background           historique   
88  background             2nd plan   
89       child        enfant unique   
90       child        enfant unique   
91       child        enfant unique   
92       child        enfant unique   
93   childhood              enfance   
94  dependable               fiable   
95  dependable               fiable   
96  dependable   digne de confiance   
97  everything        tout le reste   
98  everything                 tout   
99  grandchild           petit-fils   

                                           l1_context                     l2  \
0   necessary | writing case | The Army needs men ...            необходимые   
1   necessary | writing case | The Army needs men ...            обязательно   
2   necessary | writing case | The Army needs men ...                  нужно   
3   necessary | writing case | The Army needs men ...              требуется   
4   necessary | writing case | The Army needs men ...                   надо   
5   if necessary | necessary | If necessary, we’ll...            необходимые   
6                                        necessary |             необходимые   
7   necessary | inevitable | unavoidable | inescap...            необходимые   
8   set out | go | start | get off | go off | star...                  пойти   
9   set out | go | start | get off | go off | star...                перейти   
10  set out | go | start | get off | go off | star...                    иди   
11  set out | go | start | get off | go off | star...                  идете   
12  set out | go | start | get off | go off | star...                  пошел   
13  set out | go | start | get off | go off | star...            отправиться   
14                                              go |                    идти   
15                                              go |             отправиться   
16                             get into | go | fit |                    идут   
17                             get into | go | fit |                 поехать   
18                             get into | go | fit |             от

In [47]:
df_all_words_azure.to_csv("azure_ctx_merge_mean_top_sim.csv")